In [124]:
import os
import folium
import json
import pandas as pd
from branca.colormap import linear
import numpy as np
from shapely.geometry import Polygon
from shapely.geometry import Point
from numpy import random

In [125]:
# dataset name
dataset_pop_2017 = os.path.join('data', 'population_2017.csv')

# read the data to a dataframe
data2017 = pd.read_csv(dataset_pop_2017)

# replace spaces for underlines in name of columns
data2017.columns = [cols.replace(' ', '_') for cols in data2017.columns]

#print the first five rows
data2017.head()

UF  COD._UF  COD._MUNIC      NOME_DO_MUNICÍPIO  POPULAÇÃO_ESTIMADA
0  RO     11.0        15.0  Alta Floresta D'Oeste             25437.0
1  RO     11.0        23.0              Ariquemes            107345.0
2  RO     11.0        31.0                 Cabixi              6224.0
3  RO     11.0        49.0                 Cacoal             88507.0
4  RO     11.0        56.0             Cerejeiras             17934.0

In [ ]:
# filtering data about RN state
dataRN = data2017[data2017['UF'] == 'RN']

# sort dataset by city name
dataRN = dataRN.sort_values('NOME_DO_MUNICÍPIO')

dataRN.head()


In [ ]:
dataPB = data2017[data2017['UF'] == 'PB']

dataPB = dataPB.sort_values('NOME_DO_MUNICÍPIO')

dataPB.loc[ dataPB[ dataPB['NOME_DO_MUNICÍPIO'] == 'Quixaba' ].index, 'NOME_DO_MUNICÍPIO'] = 'Quixabá'
dataPB.loc[ dataPB[ dataPB['NOME_DO_MUNICÍPIO'] == 'Joca Claudino' ].index, 'NOME_DO_MUNICÍPIO'] = 'Santarém'
dataPB.loc[ dataPB[ dataPB['NOME_DO_MUNICÍPIO'] == 'São Vicente do Seridó' ].index, 'NOME_DO_MUNICÍPIO'] = 'Seridó'
dataPB.loc[ dataPB[ dataPB['NOME_DO_MUNICÍPIO'] == 'Tacima' ].index, 'NOME_DO_MUNICÍPIO'] = 'Campo de Santana'

dataPB.head()



In [ ]:
# searching the files in geojson/geojs-xx-mun.json
geo_json_rn_path = os.path.join('geojson', 'geojs-24-mun.json')

# load the data and use 'latin-1'encoding because the accent
geo_json_data_rn = json.load(open(geo_json_rn_path,encoding='latin-1'))

geo_json_data_rn

In [ ]:
# searching the files in geojson/geojs-xx-mun.json
geo_json_pb_path = os.path.join('geojson', 'geojs-25-mun.json')

# load the data and use 'latin-1'encoding because the accent
geo_json_data_pb = json.load(open(geo_json_pb_path,encoding='latin-1'))

geo_json_data_pb

In [ ]:
# http://cidades.ibge.gov.br/painel/historico.php?codmun=241030
# Presidente Juscelino city changes your name to Serra Caiada
geo_json_data_rn['features'][112]['properties']['description'] = 'Serra Caiada'
geo_json_data_rn['features'][112]['properties']['name'] = 'Serra Caiada'

In [ ]:
# Create a map object
'''m = folium.Map(
    location=[-5.826592, -35.212558],
    zoom_start=7,
    tiles='Stamen Terrain'
)

# Configure geojson layer
folium.GeoJson(geo_json_data_rn).add_to(m)

m'''

In [ ]:
# Configure geojson layer
'''folium.GeoJson(geo_json_data_pb).add_to(m)

m'''

In [ ]:
# colormap yellow and green (YlGn)
colormap_rn = linear.YlGn.scale(
    dataRN.POPULAÇÃO_ESTIMADA.min(),
    dataRN.POPULAÇÃO_ESTIMADA.max())

colormap_rn

In [ ]:
# colormap orange and red (OrRd)
colormap_pb = linear.GnBu.scale(
    dataPB.POPULAÇÃO_ESTIMADA.min(),
    dataPB.POPULAÇÃO_ESTIMADA.max())

colormap_pb

In [ ]:
population_dict_rn = dataRN.set_index('NOME_DO_MUNICÍPIO')['POPULAÇÃO_ESTIMADA']

# create a threshold of legend
threshold_scale_rn = np.linspace(dataRN['POPULAÇÃO_ESTIMADA'].min(),
                              dataRN['POPULAÇÃO_ESTIMADA'].max(), 6, dtype=int).tolist()

In [ ]:
population_dict_pb = dataPB.set_index('NOME_DO_MUNICÍPIO')['POPULAÇÃO_ESTIMADA']

# create a threshold of legend
threshold_scale_pb = np.linspace(dataPB['POPULAÇÃO_ESTIMADA'].min(),
                              dataPB['POPULAÇÃO_ESTIMADA'].max(), 6, dtype=int).tolist()

In [ ]:
m = folium.Map(
    location=[-5.826592, -35.212558],
    zoom_start=7,
    tiles='Stamen Terrain'
)

In [ ]:
folium.GeoJson(
    geo_json_data_rn,
    name='Population estimation of RN State in 2017',
    style_function=lambda feature: {
        'fillColor': colormap_rn(population_dict_rn[feature['properties']['description']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.4,
    }
).add_to(m)

colormap_rn.caption = 'Population estimation of RN State in 2017'
colormap_rn.add_to(m)

m

In [ ]:
m.choropleth(
    geo_data=geo_json_data_rn,
    data=dataRN,
    columns=['NOME_DO_MUNICÍPIO', 'POPULAÇÃO_ESTIMADA'],
    key_on='feature.properties.description',
    fill_color='YlGn',
    legend_name='Population estimation of RN State in 2017',
    highlight=True,
    threshold_scale = threshold_scale_rn
)

m

In [ ]:
folium.GeoJson(
    geo_json_data_pb,
    name='Population estimation of PB State in 2017',
    style_function=lambda feature: {
        'fillColor': colormap_pb(population_dict_pb[feature['properties']['description']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '1, 1',
        'fillOpacity': 0.4,
    }
).add_to(m)

colormap_pb.caption = 'Population estimation of PB State in 2017'
colormap_pb.add_to(m)

m

In [ ]:

m.choropleth(
    geo_data=geo_json_data_pb,
    data=dataPB,
    columns=['NOME_DO_MUNICÍPIO', 'POPULAÇÃO_ESTIMADA'],
    key_on='feature.properties.description',
    fill_color='GnBu',
    legend_name='Population estimation of PB State in 2017',
    highlight=True,
    threshold_scale = threshold_scale_pb
)

m

In [ ]:
folium.LayerControl().add_to(m)

m

In [126]:
states = ['MA', 'PI', 'CE', 'RN', 'PB', 'PE', 'AL', 'SE', 'BA']
data = {}

for i in states:
    data[i] = data2017[data2017['UF'] == i]
    data[i] = data[i].sort_values('NOME_DO_MUNICÍPIO')


In [127]:
fill_colors = ['BuGn', 'OrRd', 'PuBu', 'GnBu', 'BuGn', 'OrRd', 'PuBu', 'GnBu', 'BuGn']

In [128]:
data['RN'][:].loc[ data['RN'][ data['RN']['NOME_DO_MUNICÍPIO'] == 'Serra Caiada' ].index, 
                  'NOME_DO_MUNICÍPIO'] = 'Presidente Juscelino'

In [129]:
data['PB'][:].loc[ data['PB'][ data['PB']['NOME_DO_MUNICÍPIO'] == 'Quixaba' ].index, 
                  'NOME_DO_MUNICÍPIO'] = 'Quixabá'
data['PB'][:].loc[ data['PB'][ data['PB']['NOME_DO_MUNICÍPIO'] == 'Joca Claudino' ].index, 
                  'NOME_DO_MUNICÍPIO'] = 'Santarém'
data['PB'][:].loc[ data['PB'][ data['PB']['NOME_DO_MUNICÍPIO'] == 'São Vicente do Seridó' ].index, 
                  'NOME_DO_MUNICÍPIO'] = 'Seridó'
data['PB'][:].loc[ data['PB'][ data['PB']['NOME_DO_MUNICÍPIO'] == 'Tacima' ].index, 
                  'NOME_DO_MUNICÍPIO'] = 'Campo de Santana'

In [130]:
geo_json_data = {}
j = 21
for i in states:
    filename = 'geojs-' + str(j) +'-mun.json'
    path = os.path.join('geojson', filename)  
    
    geo_json_data[i] = json.load(open(path, encoding='latin-1'))
    
    j = j+1
    


In [131]:
threshold_scales = {}

for i in states:
    threshold_scales[i] = np.linspace(data[i]['POPULAÇÃO_ESTIMADA'].min(),
                              data[i]['POPULAÇÃO_ESTIMADA'].max(), 6, dtype=int).tolist()


In [132]:
m = folium.Map(
    location=[-5.826592, -35.212558],
    zoom_start=5,
    tiles='Stamen Terrain'
)

j = 0;
for i in states:
    m.choropleth(
        geo_data=geo_json_data[i],
        data=data[i],
        columns=['NOME_DO_MUNICÍPIO', 'POPULAÇÃO_ESTIMADA'],
        key_on='feature.properties.description',
        fill_color= fill_colors[j],
        #fill_color = 'OrRd',
        legend_name='Population estimation of ' + i + ' State in 2017',
        highlight=True,
        threshold_scale = threshold_scales[i]
    )
    
    j=j+1
    


In [133]:
folium.LayerControl().add_to(m)

m